In [1]:
import numpy as np

import time
import mujoco
import mujoco.viewer

import mujoco
import numpy as np
import matplotlib.pyplot as plt
import mujoco.viewer

import mediapy as media
import time

import matplotlib.pyplot as plt
from scipy.linalg import null_space
from scipy.spatial.transform import Rotation as R

In [2]:
from main_2sept import LeapNodeMujoco, GraspClass
from inv_kin import GradientDescentIK, OnlyPosIK

model_path = '/home/sysidea/leap_hand_mujoco/model/leap hand/leaphand_2.9.24.xml'
leap_hand = LeapNodeMujoco(model_path)

IK_index=GradientDescentIK('/home/sysidea/leap_hand_mujoco/model/leap hand/index_finger.xml')
IK_thumb=GradientDescentIK('/home/sysidea/leap_hand_mujoco/model/leap hand/thumb.xml')
IK_thumb_pos=OnlyPosIK('/home/sysidea/leap_hand_mujoco/model/leap hand/thumb.xml')
IK_middle=OnlyPosIK('/home/sysidea/leap_hand_mujoco/model/leap hand/middle.xml')
IK_tertiary=OnlyPosIK('/home/sysidea/leap_hand_mujoco/model/leap hand/tertiary.xml')

In [3]:
camera1 = mujoco.MjvCamera()
mujoco.mjv_defaultFreeCamera(leap_hand.m, camera1)

# Set camera position
camera1.lookat[:] = np.array([0.0, 0.0, 0.0])  # Point in space the camera is looking at
camera1.azimuth = -90                # Horizontal angle in degrees
camera1.elevation = -10                      # Vertical angle in degrees
camera1.distance = 1                         # Distance from the lookat point

camera2 = mujoco.MjvCamera()
mujoco.mjv_defaultFreeCamera(leap_hand.m, camera2)

# Set camera position
camera2.lookat[:] = np.array([0.0, 0.0, 0.0])  # Point in space the camera is looking at
camera2.azimuth = 0               # Horizontal angle in degrees
camera2.elevation = -90                      # Vertical angle in degrees
camera2.distance = 1                         # Distance from the lookat point

camera3 = mujoco.MjvCamera()
mujoco.mjv_defaultFreeCamera(leap_hand.m, camera3)

# Set camera position
camera3.lookat[:] = np.array([0.0, 0.0, 0.15])  # Point in space the camera is looking at
camera3.azimuth = 90               # Horizontal angle in degrees
camera3.elevation = -15                      # Vertical angle in degrees
camera3.distance = 1                         # Distance from the lookat point


In [4]:
mujoco.mj_step(leap_hand.m,leap_hand.d)

pos_worldi1=leap_hand.d.site(leap_hand.m.site('contact_index1').id).xpos.reshape(3)
rot_worldi1=leap_hand.d.site(leap_hand.m.site('contact_index1').id).xmat.reshape(3,3)
pos_worldt1=leap_hand.d.site(leap_hand.m.site('contact_thumb1').id).xpos.reshape(3)
rot_worldt1=leap_hand.d.site(leap_hand.m.site('contact_thumb1').id).xmat.reshape(3,3)

pos_worldi2=leap_hand.d.site(leap_hand.m.site('contact_index2').id).xpos.reshape(3)
rot_worldi2=leap_hand.d.site(leap_hand.m.site('contact_index2').id).xmat.reshape(3,3)
pos_worldt2=leap_hand.d.site(leap_hand.m.site('contact_thumb2').id).xpos.reshape(3)
rot_worldt2=leap_hand.d.site(leap_hand.m.site('contact_thumb2').id).xmat.reshape(3,3)

pos_world_palm=leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
rot_world_palm=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])

pos_palmi1=pos_worldi1-pos_world_palm
rot_palmi1=rot_world_palm.T @ rot_worldi1
pos_palmt1=pos_worldt1-pos_world_palm
rot_palmt1=rot_world_palm.T @ rot_worldt1

pos_palmi2=pos_worldi2-pos_world_palm
rot_palmi2=rot_world_palm.T @ rot_worldi2
pos_palmt2=pos_worldt1-pos_world_palm
rot_palmt2=rot_world_palm.T @ rot_worldt2


In [5]:
result_index1=IK_index.calculate(pos_palmi1, rot_palmi1,'contact_index')
result_thumb1=IK_thumb.calculate(pos_palmt1, rot_palmt1,'contact_thumb')
result_index2=IK_index.calculate(pos_palmi2, rot_palmi2,'contact_index')
result_thumb2=IK_thumb.calculate(pos_palmt2, rot_palmt2,'contact_thumb')

print("result_index1",result_index1)
print("result_thumb1",result_thumb1)
print("result_index2",result_index2)
print("result_thumb2",result_thumb2)


framerate=30

#go near the contact point
while leap_hand.d.time < 2:

    leap_hand.apply_controls_palm_z(0)
    leap_hand.apply_controls_wrist(0)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 4 and leap_hand.d.time>2:

    leap_hand.apply_controls_palm_z(0)
    leap_hand.apply_controls_wrist(0)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 6 and leap_hand.d.time>4:

    leap_hand.apply_controls_palm_z(0)
    leap_hand.apply_controls_wrist(0)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 8 and leap_hand.d.time>6:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(0)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 8.5 and leap_hand.d.time>8:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi/4)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 9 and leap_hand.d.time>8.5:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi/2)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 9.5 and leap_hand.d.time>9:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(3*np.pi/4)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 10 and leap_hand.d.time>9.5:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 11 and leap_hand.d.time>10:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 12 and leap_hand.d.time>11:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,0,0,0,0,0,0,0,0,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 13 and leap_hand.d.time>12:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand_slow([np.pi/2,0,0,0,0,0,0,0,0,0,0,0,np.pi/2,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 14 and leap_hand.d.time>13:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand_slow([np.pi/2,0,0,0,0,0,0,0,0,0,0,0,np.pi/2,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 15 and leap_hand.d.time>14:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand_slow([9*np.pi/20,0,0,0,9*np.pi/20,0,0,0,9*np.pi/20,0,0,0,np.pi/2,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 17 and leap_hand.d.time>15:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([9*np.pi/20,0,0,0,9*np.pi/20,0,0,0,9*np.pi/20,0,0,0,np.pi/2,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)


while leap_hand.d.time < 18 and leap_hand.d.time>17:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([8*np.pi/20,0,0,0,8*np.pi/20,0,0,0,8*np.pi/20,0,0,0,np.pi/2,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 20 and leap_hand.d.time>18:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,np.pi/4,0,0,0])
    
    
    #temperory
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 22 and leap_hand.d.time>20:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,np.pi/8,0,-np.pi/4,0])
    
    
    
    #temperory
    leap_hand.step_video(framerate,camera2)



while leap_hand.d.time < 24 and leap_hand.d.time>22:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,0,0,-np.pi/4,0])
    
    
    #temperory
    leap_hand.step_video(framerate,camera3)


while leap_hand.d.time < 28 and leap_hand.d.time>24:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,0,0,0,0])

    
    #temperory
    leap_hand.step_video(framerate,camera3)

leap_hand.play_video(framerate)


result_index1 [1.03637883e+00 1.84994063e-04 4.67016263e-01 6.80227245e-02]
result_thumb1 [ 1.57001343e+00 -1.89591547e-04  4.25434924e-01 -4.25023042e-01]
result_index2 [ 1.18567413e+00  1.99198418e-04  4.80134061e-01 -9.43587590e-02]
result_thumb2 [ 1.57001343e+00 -1.89591547e-04  4.25434924e-01 -4.25023042e-01]
Total frames captured: 841


This browser does not support the video tag.


In [6]:

mujoco.mj_step(leap_hand.m,leap_hand.d)

Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w=leap_hand.d.site_xpos[4].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push=np.dot(Rpalm_w.T,P_push_w)
    
result_push=IK_thumb_pos.calculate(P_push,'contact_thumb_end')

print("result_push",result_push)

while leap_hand.d.time < 32 and leap_hand.d.time>28:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_push
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,a,b,c,d])
    
    
    #temperory
    leap_hand.step_video(framerate,camera2)

mujoco.mj_step(leap_hand.m,leap_hand.d)

Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w=leap_hand.d.site_xpos[5].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push=np.dot(Rpalm_w.T,P_push_w)
    
result_push=IK_thumb_pos.calculate(P_push,'contact_thumb_end')
print("result_push",result_push)


while leap_hand.d.time < 34 and leap_hand.d.time>32:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_push
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand_slow([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,a,b,c,d])
    
    #temperory
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 38 and leap_hand.d.time>34:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_push
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand_slow([7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,7*np.pi/20,0,0,0,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera2)
    
leap_hand.play_video(framerate)

result_push [ 0.51195958  0.21983941 -0.34789641  1.26686096]
result_push [0.42515816 0.97037342 0.35358706 1.7871685 ]
Total frames captured: 1141


This browser does not support the video tag.


In [7]:
mujoco.mj_step(leap_hand.m,leap_hand.d)
Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w_t=leap_hand.d.site_xpos[6].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_t=np.dot(Rpalm_w.T,P_push_w_t)
    
result_grip_t=IK_tertiary.calculate(P_push_t,'contact_tertiary')

P_push_w_m=leap_hand.d.site_xpos[7].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_m=np.dot(Rpalm_w.T,P_push_w_m)
    
result_grip_m=IK_middle.calculate(P_push_m,'contact_middle')

print("result_grip_t",result_grip_t)
print("result_grip_m",result_grip_m)


while leap_hand.d.time < 39 and leap_hand.d.time>38:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    leap_hand.step_video(framerate,camera2)

mujoco.mj_step(leap_hand.m,leap_hand.d)
Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w_t=leap_hand.d.site_xpos[6].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_t=np.dot(Rpalm_w.T,P_push_w_t)
    
result_grip_t=IK_tertiary.calculate(P_push_t,'contact_tertiary')

P_push_w_m=leap_hand.d.site_xpos[7].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_m=np.dot(Rpalm_w.T,P_push_w_m)
    
result_grip_m=IK_middle.calculate(P_push_m,'contact_middle')

print("result_grip_t",result_grip_t)
print("result_grip_m",result_grip_m)

while leap_hand.d.time < 40 and leap_hand.d.time>39:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera2)

mujoco.mj_step(leap_hand.m,leap_hand.d)
Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w_t=leap_hand.d.site_xpos[6].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_t=np.dot(Rpalm_w.T,P_push_w_t)
    
result_grip_t=IK_tertiary.calculate(P_push_t,'contact_tertiary')

P_push_w_m=leap_hand.d.site_xpos[7].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_m=np.dot(Rpalm_w.T,P_push_w_m)
    
result_grip_m=IK_middle.calculate(P_push_m,'contact_middle')

print("result_grip_t",result_grip_t)
print("result_grip_m",result_grip_m)

while leap_hand.d.time < 41 and leap_hand.d.time>40:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

mujoco.mj_step(leap_hand.m,leap_hand.d)
Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w_t=leap_hand.d.site_xpos[6].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_t=np.dot(Rpalm_w.T,P_push_w_t)
    
result_grip_t=IK_tertiary.calculate(P_push_t,'contact_tertiary')

P_push_w_m=leap_hand.d.site_xpos[7].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_m=np.dot(Rpalm_w.T,P_push_w_m)
    
result_grip_m=IK_middle.calculate(P_push_m,'contact_middle')

print("result_grip_t",result_grip_t)
print("result_grip_m",result_grip_m)

while leap_hand.d.time < 45 and leap_hand.d.time>41:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

mujoco.mj_step(leap_hand.m,leap_hand.d)
Rpalm_w=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])
P_push_w_t=leap_hand.d.site_xpos[8].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_t=np.dot(Rpalm_w.T,P_push_w_t)
    
result_grip_t=IK_tertiary.calculate(P_push_t,'contact_tertiary')

P_push_w_m=leap_hand.d.site_xpos[9].reshape(3)-leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
P_push_m=np.dot(Rpalm_w.T,P_push_w_m)
    
result_grip_m=IK_middle.calculate(P_push_m,'contact_middle')

print("result_grip_t",result_grip_t)
print("result_grip_m",result_grip_m)

while leap_hand.d.time < 50 and leap_hand.d.time>45:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)
    
leap_hand.play_video(framerate)

result_grip_t [ 0.93512485 -0.11610709  1.14659567  0.93338226]
result_grip_m [ 0.92345344 -0.1179225   1.15230915  0.9406219 ]
result_grip_t [ 0.98540091 -0.08656483  1.13714751  0.88141461]
result_grip_m [ 0.97582495 -0.09015934  1.13734818  0.88064051]
result_grip_t [ 0.98343987 -0.08911568  1.13306338  0.87833856]
result_grip_m [ 0.97322369 -0.09217513  1.13584675  0.88048616]
result_grip_t [ 0.99545618 -0.08734627  1.13245347  0.87273073]
result_grip_m [ 0.98550649 -0.0903911   1.13506841  0.87462809]
result_grip_t [ 0.98941098 -0.05914647  1.23300826  0.97792993]
result_grip_m [ 0.97771655 -0.06100874  1.23818657  0.98267638]
Total frames captured: 1501


This browser does not support the video tag.


In [8]:
while leap_hand.d.time < 52 and leap_hand.d.time>50:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(np.pi/2)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

while leap_hand.d.time < 54 and leap_hand.d.time>52:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(0)

    #placeholder code 
    #index finger
    [a,b,c,d]=result_grip_m
    [e,f,g,h]=result_grip_t
    
    leap_hand.apply_controls_hand([7*np.pi/20,0,0,0,a,b,c,d,e,f,g,h,0,0,0,0])
    
    #temperory
    leap_hand.step_video(framerate,camera1)


leap_hand.play_video(framerate)

Total frames captured: 1621


This browser does not support the video tag.


In [9]:

while leap_hand.d.time < 56 and leap_hand.d.time>54:

    leap_hand.apply_controls_palm_z(0.15)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([0,0,0,0,a1,b1,c1,d1,e1,f1,g1,h1,0,0,0,0])
    
    leap_hand.step_video(framerate,camera1)


    
leap_hand.play_video(framerate)

Total frames captured: 1681


This browser does not support the video tag.


In [10]:
while leap_hand.d.time < 57 and leap_hand.d.time>56:

    leap_hand.apply_controls_palm_z(0.3)
    # leap_hand.d.apply_controls_y(-0.255)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([0,0,0,0,a1,b1,c1,d1,e1,f1,g1,h1,0,0,0,0])
    
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 58 and leap_hand.d.time>57:

    leap_hand.apply_controls_palm_z(0.3)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([0,0,0,0,a1,b1,c1,d1,e1,f1,g1,h1,0,0,0,0])
    
    leap_hand.step_video(framerate,camera2)

while leap_hand.d.time < 62 and leap_hand.d.time>58:

    leap_hand.apply_controls_palm_z(0.3)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([0,0,0,0,a1,b1,c1,d1,e1,f1,g1,h1,0,0,0,0])
    
    leap_hand.step_video(framerate,camera2)



    
leap_hand.play_video(framerate)

Total frames captured: 1861


This browser does not support the video tag.


In [11]:
while leap_hand.d.time < 66 and leap_hand.d.time>62:

    leap_hand.apply_controls_palm_z(0.09)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([0,0,0,0,a1,b1,c1,d1,e1,f1,g1,h1,0,0,0,0])
    
    leap_hand.step_video(framerate,camera1)



    
leap_hand.play_video(framerate)

Total frames captured: 1981


This browser does not support the video tag.


In [12]:
mujoco.mj_step(leap_hand.m,leap_hand.d)

pos_worldi0=leap_hand.d.site(leap_hand.m.site('contact_index0_big').id).xpos.reshape(3)
rot_worldi0=leap_hand.d.site(leap_hand.m.site('contact_index0_big').id).xmat.reshape(3,3)
pos_worldt0=leap_hand.d.site(leap_hand.m.site('contact_thumb0_big').id).xpos.reshape(3)
rot_worldt0=leap_hand.d.site(leap_hand.m.site('contact_thumb0_big').id).xmat.reshape(3,3)

pos_worldi1=leap_hand.d.site(leap_hand.m.site('contact_index1_big').id).xpos.reshape(3)
rot_worldi1=leap_hand.d.site(leap_hand.m.site('contact_index1_big').id).xmat.reshape(3,3)
pos_worldt1=leap_hand.d.site(leap_hand.m.site('contact_thumb1_big').id).xpos.reshape(3)
rot_worldt1=leap_hand.d.site(leap_hand.m.site('contact_thumb1_big').id).xmat.reshape(3,3)

pos_worldi2=leap_hand.d.site(leap_hand.m.site('contact_index2_big').id).xpos.reshape(3)
rot_worldi2=leap_hand.d.site(leap_hand.m.site('contact_index2_big').id).xmat.reshape(3,3)
pos_worldt2=leap_hand.d.site(leap_hand.m.site('contact_thumb2_big').id).xpos.reshape(3)
rot_worldt2=leap_hand.d.site(leap_hand.m.site('contact_thumb2_big').id).xmat.reshape(3,3)

pos_world_palm=leap_hand.d.body(leap_hand.m.body('palm').id).xpos.reshape(3)
rot_world_palm=np.reshape(leap_hand.d.body(leap_hand.m.body('palm').id).xmat,[3,3])

pos_palmi0=pos_worldi0-pos_world_palm
rot_palmi0=rot_world_palm.T @ rot_worldi0
pos_palmt0=pos_worldt0-pos_world_palm
rot_palmt0=rot_world_palm.T @ rot_worldt0

pos_palmi1=pos_worldi1-pos_world_palm
rot_palmi1=rot_world_palm.T @ rot_worldi1
pos_palmt1=pos_worldt1-pos_world_palm
rot_palmt1=rot_world_palm.T @ rot_worldt1

pos_palmi2=pos_worldi2-pos_world_palm
rot_palmi2=rot_world_palm.T @ rot_worldi2
pos_palmt2=pos_worldt1-pos_world_palm
rot_palmt2=rot_world_palm.T @ rot_worldt2


In [13]:
result_index0=IK_index.calculate(pos_palmi0, rot_palmi0,'contact_index')
result_thumb0=IK_thumb.calculate(pos_palmt0, rot_palmt0,'contact_thumb')


print("result_index0",result_index0)
print("result_thumb0",result_thumb0)


framerate=30

#go near the contact point
while leap_hand.d.time < 68 and leap_hand.d.time>66:

    leap_hand.apply_controls_palm_z(0.09)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t
    [a,b,c,d]=result_index0
    [e,f,g,h]=result_thumb0

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,a1,b1,c1,d1,e1,f1,g1,h1,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

leap_hand.play_video(framerate)

result_index0 [ 0.5741855   0.00391044  1.01473456 -0.07997615]
result_thumb0 [ 1.57660345e+00  3.05378516e-04 -1.13998221e-01  1.76467628e-01]
Total frames captured: 2041


This browser does not support the video tag.


In [14]:
result_index1=IK_index.calculate(pos_palmi1, rot_palmi1,'contact_index')
result_thumb1=IK_thumb.calculate(pos_palmt1, rot_palmt1,'contact_thumb')
print("result_index1",result_index1)
print("result_thumb1",result_thumb1)
while leap_hand.d.time < 70 and leap_hand.d.time>68:

    leap_hand.apply_controls_palm_z(0.09)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t
    [a,b,c,d]=result_index1
    [e,f,g,h]=result_thumb1

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,a1,b1,c1,d1,e1,f1,g1,h1,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

leap_hand.play_video(framerate)

result_index1 [ 0.58034804  0.00393128  1.06045321 -0.13185685]
result_thumb1 [ 1.57660334e+00  2.96228834e-04 -1.05423135e-02  7.28843375e-02]
Total frames captured: 2101


This browser does not support the video tag.


In [15]:
result_index2=IK_index.calculate(pos_palmi2, rot_palmi2,'contact_index')
result_thumb2=IK_thumb.calculate(pos_palmt2, rot_palmt2,'contact_thumb')

print("result_index2",result_index2)
print("result_thumb2",result_thumb2)
while leap_hand.d.time < 72 and leap_hand.d.time>70:

    leap_hand.apply_controls_palm_z(0.09)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,a1,b1,c1,d1,e1,f1,g1,h1,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

leap_hand.play_video(framerate)

result_index2 [ 0.58880291  0.00396438  1.10203715 -0.18189506]
result_thumb2 [ 1.57660334e+00  2.96228834e-04 -1.05423135e-02  7.28843375e-02]
Total frames captured: 2161


This browser does not support the video tag.


In [16]:
while leap_hand.d.time < 76 and leap_hand.d.time>72:

    leap_hand.apply_controls_palm_z(0.2)
    leap_hand.apply_controls_palm_y(-0.260)
    leap_hand.apply_controls_wrist(0)

    [a1,b1,c1,d1]=result_grip_m
    [e1,f1,g1,h1]=result_grip_t
    [a,b,c,d]=result_index2
    [e,f,g,h]=result_thumb2

    # [a,b,c,d]=result_index1
    # [e,f,g,h]=result_thumb1
    
    leap_hand.apply_controls_hand([a,b,c,d,a1,b1,c1,d1,e1,f1,g1,h1,e,f,g,h])
    
    #temperory
    leap_hand.step_video(framerate,camera1)

leap_hand.play_video(framerate)

Total frames captured: 2281


This browser does not support the video tag.
